# 20 Newsgroups Data

## Problem Description

This data set consists of 20000 messages taken from 20 newsgroups. Approximately 4% of the articles are crossposted. The articles are typical postings and thus have headers including subject lines, signature files, and quoted portions of other articles.
We need to classify each newgroup to their domain given: 
 - Each newsgroup file in the bundle represents a single newsgroup
 - Each message in a file is the text of some newsgroup document that was posted to that newsgroup.

## Importing the relevant libraries

In [1]:
# Loading Packages
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np
from sklearn.datasets import fetch_20newsgroups
import pandas as pd

## Loading Data

In [2]:
%%time

import os

docs=[]
labels=[]
label_index={}

PATH=os.getcwd()

text_data_dir=os.path.join(PATH,'20_newsgroups')
for name in os.listdir(text_data_dir):
    path=os.path.join(text_data_dir,name)
    if os.path.isdir(path):
        label_id=len(label_index)
        label_index[label_id]=name
        for fname in sorted(os.listdir(path)):
            fpath=os.path.join(path,fname)
            f=open(fpath,encoding="ISO-8859-1")
            t=f.read()
            docs.append(t)
            f.close()
            labels.append(label_id)

print('Found %s docs.' %len(docs))
        


Found 19997 docs.
Wall time: 3.31 s


In [3]:
label_index          # Getting labels

{0: 'alt.atheism',
 1: 'comp.graphics',
 2: 'comp.os.ms-windows.misc',
 3: 'comp.sys.ibm.pc.hardware',
 4: 'comp.sys.mac.hardware',
 5: 'comp.windows.x',
 6: 'misc.forsale',
 7: 'rec.autos',
 8: 'rec.motorcycles',
 9: 'rec.sport.baseball',
 10: 'rec.sport.hockey',
 11: 'sci.crypt',
 12: 'sci.electronics',
 13: 'sci.med',
 14: 'sci.space',
 15: 'soc.religion.christian',
 16: 'talk.politics.guns',
 17: 'talk.politics.mideast',
 18: 'talk.politics.misc',
 19: 'talk.religion.misc'}

In [4]:
type(docs)

list

In [5]:
data = pd.DataFrame(docs)   # Converting to DataFrame from list

In [6]:
data.head()

0
0  Xref: cantaloupe.srv.cs.cmu.edu alt.atheism:49...
1  Xref: cantaloupe.srv.cs.cmu.edu alt.atheism:51...
2  Newsgroups: alt.atheism\nPath: cantaloupe.srv....
3  Xref: cantaloupe.srv.cs.cmu.edu alt.atheism:51...
4  Xref: cantaloupe.srv.cs.cmu.edu alt.atheism:51...

In [7]:
data['target'] = labels

In [8]:
data.columns=['text','target']

In [9]:
data.shape

(19997, 2)

In [10]:
#Duplicating the original text extracted before proceeding with preprocessing steps

import copy
print(type(data['text']))
original_data = copy.deepcopy(data)
print(data.keys())
print(original_data.keys())

<class 'pandas.core.series.Series'>
Index(['text', 'target'], dtype='object')
Index(['text', 'target'], dtype='object')


## Basic cleaning of text

### LowerCase all text

In [11]:
data['text'] = [text.strip().lower() for text in data['text']]
data['text'][:10]  #Checking first 10 rows

0    xref: cantaloupe.srv.cs.cmu.edu alt.atheism:49...
1    xref: cantaloupe.srv.cs.cmu.edu alt.atheism:51...
2    newsgroups: alt.atheism\npath: cantaloupe.srv....
3    xref: cantaloupe.srv.cs.cmu.edu alt.atheism:51...
4    xref: cantaloupe.srv.cs.cmu.edu alt.atheism:51...
5    newsgroups: alt.atheism\npath: cantaloupe.srv....
6    path: cantaloupe.srv.cs.cmu.edu!crabapple.srv....
7    newsgroups: alt.atheism\npath: cantaloupe.srv....
8    path: cantaloupe.srv.cs.cmu.edu!crabapple.srv....
9    path: cantaloupe.srv.cs.cmu.edu!crabapple.srv....
Name: text, dtype: object

## Defining the functions to perform basic steps like 

- **expanding contractions**
 
- **remove accented characters**

- **scrub words**

In [12]:
type(data['text'])

pandas.core.series.Series

###  Handling contractions 

In [13]:
contractions = {
"ain't": "is not",
"aren't": "are not",
"can't": "cannot",
"can't've": "cannot have",
"'cause": "because",
"could've": "could have",
"couldn't": "could not",
"couldn't've": "could not have",
"didn't": "did not",
"doesn't": "does not",
"don't": "do not",
"hadn't": "had not",
"hadn't've": "had not have",
"hasn't": "has not",
"haven't": "have not",
"he'd": "he would",
"he'd've": "he would have",
"he'll": "he will",
"he'll've": "he he will have",
"he's": "he is",
"how'd": "how did",
"how'd'y": "how do you",
"how'll": "how will",
"how's": "how is",
"I'd": "I would",
"I'd've": "I would have",
"I'll": "I will",
"I'll've": "I will have",
"I'm": "I am",
"I've": "I have",
"i'd": "i would",
"i'd've": "i would have",
"i'll": "i will",
"i'll've": "i will have",
"i'm": "i am",
"i've": "i have",
"isn't": "is not",
"it'd": "it would",
"it'd've": "it would have",
"it'll": "it will",
"it'll've": "it will have",
"it's": "it is",
"let's": "let us",
"ma'am": "madam",
"mayn't": "may not",
"might've": "might have",
"mightn't": "might not",
"mightn't've": "might not have",
"must've": "must have",
"mustn't": "must not",
"mustn't've": "must not have",
"needn't": "need not",
"needn't've": "need not have",
"o'clock": "of the clock",
"oughtn't": "ought not",
"oughtn't've": "ought not have",
"shan't": "shall not",
"sha'n't": "shall not",
"shan't've": "shall not have",
"she'd": "she would",
"she'd've": "she would have",
"she'll": "she will",
"she'll've": "she will have",
"she's": "she is",
"should've": "should have",
"shouldn't": "should not",
"shouldn't've": "should not have",
"so've": "so have",
"so's": "so as",
"that'd": "that would",
"that'd've": "that would have",
"that's": "that is",
"there'd": "there would",
"there'd've": "there would have",
"there's": "there is",
"they'd": "they would",
"they'd've": "they would have",
"they'll": "they will",
"they'll've": "they will have",
"they're": "they are",
"they've": "they have",
"to've": "to have",
"wasn't": "was not",
"we'd": "we would",
"we'd've": "we would have",
"we'll": "we will",
"we'll've": "we will have",
"we're": "we are",
"we've": "we have",
"weren't": "were not",
"what'll": "what will",
"what'll've": "what will have",
"what're": "what are",
"what's": "what is",
"what've": "what have",
"when's": "when is",
"when've": "when have",
"where'd": "where did",
"where's": "where is",
"where've": "where have",
"who'll": "who will",
"who'll've": "who will have",
"who's": "who is",
"who've": "who have",
"why's": "why is",
"why've": "why have",
"will've": "will have",
"won't": "will not",
"won't've": "will not have",
"would've": "would have",
"wouldn't": "would not",
"wouldn't've": "would not have",
"y'all": "you all",
"y'all'd": "you all would",
"y'all'd've": "you all would have",
"y'all're": "you all are",
"y'all've": "you all have",
"you'd": "you would",
"you'd've": "you would have",
"you'll": "you will",
"you'll've": "you will have",
"you're": "you are",
"you've": "you have"
}

In [14]:
def expand_contractions(text):
    for word in text.split():
        if word.lower() in contractions:
            text = text.replace(word, contractions[word.lower()])
    return text

In [15]:
import re
data['text'] = [expand_contractions(re.sub('’', "'", text)) for text in data['text']]
data['text'][1]

'xref: cantaloupe.srv.cs.cmu.edu alt.atheism:51060 alt.atheism.moderated:727 news.answers:7300 alt.answers:155\npath: cantaloupe.srv.cs.cmu.edu!crabapple.srv.cs.cmu.edu!fs7.ece.cmu.edu!europa.eng.gtefsd.com!howland.reston.ans.net!agate!netsys!ibmpcug!mantis!mathew\nfrom: mathew <mathew@mantis.co.uk>\nnewsgroups: alt.atheism,alt.atheism.moderated,news.answers,alt.answers\nsubject: alt.atheism faq: introduction to atheism\nsummary: please read this file before posting to alt.atheism\nkeywords: faq, atheism\nmessage-id: <19930405122245@mantis.co.uk>\ndate: mon, 5 apr 1993 12:22:45 gmt\nexpires: thu, 6 may 1993 12:22:45 gmt\nfollowup-to: alt.atheism\ndistribution: world\norganization: mantis consultants, cambridge. uk.\napproved: news-answers-request@mit.edu\nsupersedes: <19930308134439@mantis.co.uk>\nlines: 646\n\narchive-name: atheism/introduction\nalt-atheism-archive-name: introduction\nlast-modified: 5 april 1993\nversion: 1.2\n\n-----begin pgp signed message-----\n\n                  

## Invoking the remove_accented_chars() function

In [16]:
data['text'][2]

'newsgroups: alt.atheism\npath: cantaloupe.srv.cs.cmu.edu!crabapple.srv.cs.cmu.edu!fs7.ece.cmu.edu!europa.eng.gtefsd.com!howland.reston.ans.net!usc!sdd.hp.com!nigel.msen.com!yale.edu!ira.uka.de!news.dfn.de!tubsibr!dbstu1.rz.tu-bs.de!i3150101\nfrom: i3150101@dbstu1.rz.tu-bs.de (benedikt rosenau)\nsubject: re: gospel dating\nmessage-id: <16ba711b3a.i3150101@dbstu1.rz.tu-bs.de>\nsender: postnntp@ibr.cs.tu-bs.de (mr. nntp inews entry)\norganization: technical university braunschweig, germany\nreferences: <16ba1e197.i3150101@dbstu1.rz.tu-bs.de> <65974@mimsy.umd.edu>\ndate: mon, 5 apr 1993 19:08:25 gmt\nlines: 93\n\nin article <65974@mimsy.umd.edu>\nmangoe@cs.umd.edu (charley wingate) writes:\n \n>>well, john has a quite different, not necessarily more elaborated theology.\n>>there is some evidence that he must have known luke, and that the content\n>>of q was known to him, but not in a \'canonized\' form.\n>\n>this is a new argument to me.  could you elaborate a little?\n>\n \nthe argument 

In [17]:
import unicodedata
def remove_accented_chars(text):
    text = unicodedata.normalize('NFKD', text).encode('ascii', 'ignore').decode('utf-8', 'ignore')
    #https://docs.python.org/2/library/unicodedata.html
    return text

In [18]:
data['text'] = [remove_accented_chars(text) for text in data['text']]
data['text'][2]

'newsgroups: alt.atheism\npath: cantaloupe.srv.cs.cmu.edu!crabapple.srv.cs.cmu.edu!fs7.ece.cmu.edu!europa.eng.gtefsd.com!howland.reston.ans.net!usc!sdd.hp.com!nigel.msen.com!yale.edu!ira.uka.de!news.dfn.de!tubsibr!dbstu1.rz.tu-bs.de!i3150101\nfrom: i3150101@dbstu1.rz.tu-bs.de (benedikt rosenau)\nsubject: re: gospel dating\nmessage-id: <16ba711b3a.i3150101@dbstu1.rz.tu-bs.de>\nsender: postnntp@ibr.cs.tu-bs.de (mr. nntp inews entry)\norganization: technical university braunschweig, germany\nreferences: <16ba1e197.i3150101@dbstu1.rz.tu-bs.de> <65974@mimsy.umd.edu>\ndate: mon, 5 apr 1993 19:08:25 gmt\nlines: 93\n\nin article <65974@mimsy.umd.edu>\nmangoe@cs.umd.edu (charley wingate) writes:\n \n>>well, john has a quite different, not necessarily more elaborated theology.\n>>there is some evidence that he must have known luke, and that the content\n>>of q was known to him, but not in a \'canonized\' form.\n>\n>this is a new argument to me.  could you elaborate a little?\n>\n \nthe argument 

## Invoking various scrub functions

In [19]:
def scrub_words(text):
    #Replace \xao characters in text
    text = re.sub('\xa0', ' ', text)
    
    #Replace non ascii / not words and digits
    text = re.sub("(\\W|\\d)",' ',text)
    
    #Replace new line characters and following text untill space
    text = re.sub('\n(\w*?)[\s]', '', text)
    
    #Remove html markup
    text = re.sub("<.*?>", ' ', text)
    
    #Remove extra spaces from the text
    text = re.sub("\s+", ' ', text)
    return text

In [20]:
data['text'] = [scrub_words(text) for text in data['text']]
data['text'][1]

'xref cantaloupe srv cs cmu edu alt atheism alt atheism moderated news answers alt answers path cantaloupe srv cs cmu edu crabapple srv cs cmu edu fs ece cmu edu europa eng gtefsd com howland reston ans net agate netsys ibmpcug mantis mathew from mathew mathew mantis co uk newsgroups alt atheism alt atheism moderated news answers alt answers subject alt atheism faq introduction to atheism summary please read this file before posting to alt atheism keywords faq atheism message id mantis co uk date mon apr gmt expires thu may gmt followup to alt atheism distribution world organization mantis consultants cambridge uk approved news answers request mit edu supersedes mantis co uk lines archive name atheism introduction alt atheism archive name introduction last modified april version begin pgp signed message an introduction to atheism by mathew mathew mantis co uk this article attempts to provide a general introduction to atheism whilst i have tried to be as neutral as possible regarding co

## Checking the integrity of the data after initial preprocessing steps

In [21]:
print("Data Type: ",type(original_data['text']))
print("Data Type: ",type(data['text']))

print("Length of data: ",len(original_data['text']))
print("Length of data: ",len(data['text']))

print("Original data: \n",original_data['text'][0])
print("\n\n**************************************************************************\n\n")
print("Clean data: \n",data['text'][0])

Data Type:  <class 'pandas.core.series.Series'>
Data Type:  <class 'pandas.core.series.Series'>
Length of data:  19997
Length of data:  19997
Original data: 
 Xref: cantaloupe.srv.cs.cmu.edu alt.atheism:49960 alt.atheism.moderated:713 news.answers:7054 alt.answers:126
Path: cantaloupe.srv.cs.cmu.edu!crabapple.srv.cs.cmu.edu!bb3.andrew.cmu.edu!news.sei.cmu.edu!cis.ohio-state.edu!magnus.acs.ohio-state.edu!usenet.ins.cwru.edu!agate!spool.mu.edu!uunet!pipex!ibmpcug!mantis!mathew
From: mathew <mathew@mantis.co.uk>
Newsgroups: alt.atheism,alt.atheism.moderated,news.answers,alt.answers
Subject: Alt.Atheism FAQ: Atheist Resources
Summary: Books, addresses, music -- anything related to atheism
Keywords: FAQ, atheism, books, music, fiction, addresses, contacts
Message-ID: <19930329115719@mantis.co.uk>
Date: Mon, 29 Mar 1993 11:57:19 GMT
Expires: Thu, 29 Apr 1993 11:57:19 GMT
Followup-To: alt.atheism
Distribution: world
Organization: Mantis Consultants, Cambridge. UK.
Approved: news-answers-reque

In [22]:
print("Original data: \n",original_data['text'][1])
print("\n\n**************************************************************************\n\n")
print("Clean data: \n",data['text'][1])

Original data: 
 Xref: cantaloupe.srv.cs.cmu.edu alt.atheism:51060 alt.atheism.moderated:727 news.answers:7300 alt.answers:155
Path: cantaloupe.srv.cs.cmu.edu!crabapple.srv.cs.cmu.edu!fs7.ece.cmu.edu!europa.eng.gtefsd.com!howland.reston.ans.net!agate!netsys!ibmpcug!mantis!mathew
From: mathew <mathew@mantis.co.uk>
Newsgroups: alt.atheism,alt.atheism.moderated,news.answers,alt.answers
Subject: Alt.Atheism FAQ: Introduction to Atheism
Summary: Please read this file before posting to alt.atheism
Keywords: FAQ, atheism
Message-ID: <19930405122245@mantis.co.uk>
Date: Mon, 5 Apr 1993 12:22:45 GMT
Expires: Thu, 6 May 1993 12:22:45 GMT
Followup-To: alt.atheism
Distribution: world
Organization: Mantis Consultants, Cambridge. UK.
Approved: news-answers-request@mit.edu
Supersedes: <19930308134439@mantis.co.uk>
Lines: 646

Archive-name: atheism/introduction
Alt-atheism-archive-name: introduction
Last-modified: 5 April 1993
Version: 1.2

-----BEGIN PGP SIGNED MESSAGE-----

                          

# Text Preprocessing

#### Adding new column "word_count" which specifies the number of tokens in each document

In [23]:
data['word_count'] = [len(text.split(' ')) for text in data['text']]
pd.DataFrame(data['word_count']).describe()

word_count
count  19997.000000
mean     369.937991
std      724.689806
min       48.000000
25%      178.000000
50%      252.000000
75%      372.000000
max    39436.000000

### Converting the dictionary to Dataframe 

Converting dictionary to dataframe as pandas provide better and readable subsetting options

In [24]:
data.keys()

Index(['text', 'target', 'word_count'], dtype='object')

In [25]:
data.head()

text  target  word_count
0  xref cantaloupe srv cs cmu edu alt atheism alt...       0        1772
1  xref cantaloupe srv cs cmu edu alt atheism alt...       0        5425
2  newsgroups alt atheism path cantaloupe srv cs ...       0         806
3  xref cantaloupe srv cs cmu edu alt atheism alt...       0         325
4  xref cantaloupe srv cs cmu edu alt atheism soc...       0         206

In [26]:
news_df = pd.DataFrame(data)
print("Shape: ",news_df.shape)
news_df.head(5)

Shape:  (19997, 3)


text  target  word_count
0  xref cantaloupe srv cs cmu edu alt atheism alt...       0        1772
1  xref cantaloupe srv cs cmu edu alt atheism alt...       0        5425
2  newsgroups alt atheism path cantaloupe srv cs ...       0         806
3  xref cantaloupe srv cs cmu edu alt atheism alt...       0         325
4  xref cantaloupe srv cs cmu edu alt atheism soc...       0         206

### Removing all the blogs with words_count value less than first quartile (25%) of words_count attribute

In [27]:
## Getting the first quartile value
q1 = np.percentile(news_df.word_count,25)
print(f"The first quartile value of words_count attribute is {q1}")

The first quartile value of words_count attribute is 178.0


In [28]:
news_df = news_df[news_df['word_count'] > q1]
print(f"The shape of trimmed blogs dataframe is {news_df.shape}")

The shape of trimmed blogs dataframe is (14996, 3)


#### Converting dataframe back to dictionary

In [29]:
data = news_df.reset_index().to_dict(orient='list')
print(f"The keys in the dictionary are {data.keys()}")

The keys in the dictionary are dict_keys(['index', 'text', 'target', 'word_count'])


In [30]:
print(data['text'][5])

newsgroups alt atheism path cantaloupe srv cs cmu edu crabapple srv cs cmu edu fs ece cmu edu europa eng gtefsd com howland reston ans net usc sdd hp com nigel msen com yale edu ira uka de news dfn de tubsibr dbstu rz tu bs de i from i dbstu rz tu bs de benedikt rosenau subject re a visit from the jehovah s witnesses message id ba ef i dbstu rz tu bs de sender postnntp ibr cs tu bs de mr nntp inews entry organization technical university braunschweig germany references bskendigc kd z cdc netcom com p v ainn e matt ksu ksu edu ba da i dbstu rz tu bs de apr batman bmd trw com date mon apr gmt lines in article apr batman bmd trw com jbrown batman bmd trw com writes did not you say lucifer was created with a perfect nature yes define perfect then i think you are playing the usual game here make sweeping statements like omni holy or perfect and do not note that they mean exactly what they say and that says that you must not use this terms when it leads to contradictions i m not trying to pl

In [31]:
type(data['text'])

list

## Stopwords, stemming, and tokenizing

In [32]:
#!conda install -c conda-forge spacy
#!python -m spacy download en_core_web_sm
#!pip install -U spacy
import spacy
nlp = spacy.load("en_core_web_sm")

# import en_core_web_sm
#nlp = en_core_web_sm.load()

In [33]:
data['text'][1]

'xref cantaloupe srv cs cmu edu alt atheism alt atheism moderated news answers alt answers path cantaloupe srv cs cmu edu crabapple srv cs cmu edu fs ece cmu edu europa eng gtefsd com howland reston ans net agate netsys ibmpcug mantis mathew from mathew mathew mantis co uk newsgroups alt atheism alt atheism moderated news answers alt answers subject alt atheism faq introduction to atheism summary please read this file before posting to alt atheism keywords faq atheism message id mantis co uk date mon apr gmt expires thu may gmt followup to alt atheism distribution world organization mantis consultants cambridge uk approved news answers request mit edu supersedes mantis co uk lines archive name atheism introduction alt atheism archive name introduction last modified april version begin pgp signed message an introduction to atheism by mathew mathew mantis co uk this article attempts to provide a general introduction to atheism whilst i have tried to be as neutral as possible regarding co

In [34]:
## Adding Custom stopwords to the spacy stopword list
customize_stop_words = ['xref']

for w in customize_stop_words:
    nlp.vocab[w].is_stop = True

In [35]:
## It might be surprising, but spaCy doesn't contain any function for stemming as it relies on lemmatization only. 
## Therefore, in this section, we will use NLTK for stemming.

## load nltk's SnowballStemmer as variable 'stemmer'
from nltk.stem.snowball import SnowballStemmer
stemmer = SnowballStemmer("english")

In [36]:
# Here I define a tokenizer and stemmer which returns the set of stems (excluding stop words) in the text that it is passed

def tokenize_and_stem(doc, remove_stopwords = True):
    # first tokenize by sentence, then by word to ensure that punctuation is caught as it's own token
    if remove_stopwords:
        tokens = [word.text for word in doc if not word.is_stop]
    else:
        tokens = [word.text for word in doc]

    filtered_tokens = []
    # filter out any tokens not containing letters (e.g., numeric tokens, raw punctuation)
    for token in tokens:
        if re.search('[a-zA-Z]', token):
            filtered_tokens.append(token)

    stems = [stemmer.stem(t) for t in filtered_tokens]
    return stems

def tokenize_and_lemmatize(doc, remove_stopwords = True):
    
    if remove_stopwords:
        tokens = [word for word in doc if not word.is_stop]
    else:
        tokens = [word for word in doc]
        
    filtered_tokens = []
    # filter out any tokens not containing letters (e.g., numeric tokens, raw punctuation)
    for token in tokens:
        if re.search('[a-zA-Z]', token.text):
            filtered_tokens.append(token)
            
    lemma = [t.lemma_ for t in filtered_tokens]
    return lemma


def tokenize_only(doc, remove_stopwords = True):
    
    if remove_stopwords:
        tokens = [word.text for word in doc if not word.is_stop]
    else:
        tokens = [word.text for word in doc]
    filtered_tokens = []
    # filter out any tokens not containing letters (e.g., numeric tokens, raw punctuation)
    for token in tokens:
        if re.search('[a-zA-Z]', token):
            filtered_tokens.append(token)
    return filtered_tokens

In [37]:
%%time
## We are trying to create four seperate lists for text with stop words, text without stop words,
## text with stemmed words and text with lemmatized words.

## Naming Conventions followed ####

## 'clean' word is appended to lists which do not contain stopwords

## 'all' keyword is appended to lists which contain stopwords.

## use extend so it's a big flat list of vocab

data['clean_text_stemmed'] = []
data['clean_text_lemmatized'] = []
data['text_stemmed'] = []
data['text_lemmatized'] = []

vocab_stemmed = []
allvocab_stemmed =[]

vocab_tokenized = []
allvocab_tokenized = []

vocab_lemmatized = []
allvocab_lemmatized = []


for idx,text in enumerate(data['text']):

    doc = nlp(text)
    print(f"processing {idx} document")
    words_stemmed = tokenize_and_stem(doc)
    vocab_stemmed.extend(words_stemmed)
    data['clean_text_stemmed'].append(words_stemmed)
        
    words_lemmatized = tokenize_and_lemmatize(doc)
    vocab_lemmatized.extend(words_lemmatized)
    data['clean_text_lemmatized'].append(words_lemmatized)
    
       
    allwords_stemmed = tokenize_and_stem(doc, False)
    allvocab_stemmed.extend(allwords_stemmed)
    data['text_stemmed'].append(allwords_stemmed)
    
    allwords_lemmatized = tokenize_and_lemmatize(doc, False)
    allvocab_lemmatized.extend(allwords_lemmatized)
    data['text_lemmatized'].append(allwords_lemmatized)
    
    allwords_tokenized = tokenize_only(doc,False)
    allvocab_tokenized.extend(allwords_tokenized)
    
    words_tokenized = tokenize_only(doc)
    vocab_tokenized.extend(words_tokenized)

processing 0 document
processing 1 document
processing 2 document
processing 3 document
processing 4 document
processing 5 document
processing 6 document
processing 7 document
processing 8 document
processing 9 document
processing 10 document
processing 11 document
processing 12 document
processing 13 document
processing 14 document
processing 15 document
processing 16 document
processing 17 document
processing 18 document
processing 19 document
processing 20 document
processing 21 document
processing 22 document
processing 23 document
processing 24 document
processing 25 document
processing 26 document
processing 27 document
processing 28 document
processing 29 document
processing 30 document
processing 31 document
processing 32 document
processing 33 document
processing 34 document
processing 35 document
processing 36 document
processing 37 document
processing 38 document
processing 39 document
processing 40 document
processing 41 document
processing 42 document
processing 43 documen

processing 346 document
processing 347 document
processing 348 document
processing 349 document
processing 350 document
processing 351 document
processing 352 document
processing 353 document
processing 354 document
processing 355 document
processing 356 document
processing 357 document
processing 358 document
processing 359 document
processing 360 document
processing 361 document
processing 362 document
processing 363 document
processing 364 document
processing 365 document
processing 366 document
processing 367 document
processing 368 document
processing 369 document
processing 370 document
processing 371 document
processing 372 document
processing 373 document
processing 374 document
processing 375 document
processing 376 document
processing 377 document
processing 378 document
processing 379 document
processing 380 document
processing 381 document
processing 382 document
processing 383 document
processing 384 document
processing 385 document
processing 386 document
processing 387 d

processing 689 document
processing 690 document
processing 691 document
processing 692 document
processing 693 document
processing 694 document
processing 695 document
processing 696 document
processing 697 document
processing 698 document
processing 699 document
processing 700 document
processing 701 document
processing 702 document
processing 703 document
processing 704 document
processing 705 document
processing 706 document
processing 707 document
processing 708 document
processing 709 document
processing 710 document
processing 711 document
processing 712 document
processing 713 document
processing 714 document
processing 715 document
processing 716 document
processing 717 document
processing 718 document
processing 719 document
processing 720 document
processing 721 document
processing 722 document
processing 723 document
processing 724 document
processing 725 document
processing 726 document
processing 727 document
processing 728 document
processing 729 document
processing 730 d

processing 1030 document
processing 1031 document
processing 1032 document
processing 1033 document
processing 1034 document
processing 1035 document
processing 1036 document
processing 1037 document
processing 1038 document
processing 1039 document
processing 1040 document
processing 1041 document
processing 1042 document
processing 1043 document
processing 1044 document
processing 1045 document
processing 1046 document
processing 1047 document
processing 1048 document
processing 1049 document
processing 1050 document
processing 1051 document
processing 1052 document
processing 1053 document
processing 1054 document
processing 1055 document
processing 1056 document
processing 1057 document
processing 1058 document
processing 1059 document
processing 1060 document
processing 1061 document
processing 1062 document
processing 1063 document
processing 1064 document
processing 1065 document
processing 1066 document
processing 1067 document
processing 1068 document
processing 1069 document


processing 1360 document
processing 1361 document
processing 1362 document
processing 1363 document
processing 1364 document
processing 1365 document
processing 1366 document
processing 1367 document
processing 1368 document
processing 1369 document
processing 1370 document
processing 1371 document
processing 1372 document
processing 1373 document
processing 1374 document
processing 1375 document
processing 1376 document
processing 1377 document
processing 1378 document
processing 1379 document
processing 1380 document
processing 1381 document
processing 1382 document
processing 1383 document
processing 1384 document
processing 1385 document
processing 1386 document
processing 1387 document
processing 1388 document
processing 1389 document
processing 1390 document
processing 1391 document
processing 1392 document
processing 1393 document
processing 1394 document
processing 1395 document
processing 1396 document
processing 1397 document
processing 1398 document
processing 1399 document


...

processing 13418 document
processing 13419 document
processing 13420 document
processing 13421 document
processing 13422 document
processing 13423 document
processing 13424 document
processing 13425 document
processing 13426 document
processing 13427 document
processing 13428 document
processing 13429 document
processing 13430 document
processing 13431 document
processing 13432 document
processing 13433 document
processing 13434 document
processing 13435 document
processing 13436 document
processing 13437 document
processing 13438 document
processing 13439 document
processing 13440 document
processing 13441 document
processing 13442 document
processing 13443 document
processing 13444 document
processing 13445 document
processing 13446 document
processing 13447 document
processing 13448 document
processing 13449 document
processing 13450 document
processing 13451 document
processing 13452 document
processing 13453 document
processing 13454 document
processing 13455 document
processing 1

processing 13736 document
processing 13737 document
processing 13738 document
processing 13739 document
processing 13740 document
processing 13741 document
processing 13742 document
processing 13743 document
processing 13744 document
processing 13745 document
processing 13746 document
processing 13747 document
processing 13748 document
processing 13749 document
processing 13750 document
processing 13751 document
processing 13752 document
processing 13753 document
processing 13754 document
processing 13755 document
processing 13756 document
processing 13757 document
processing 13758 document
processing 13759 document
processing 13760 document
processing 13761 document
processing 13762 document
processing 13763 document
processing 13764 document
processing 13765 document
processing 13766 document
processing 13767 document
processing 13768 document
processing 13769 document
processing 13770 document
processing 13771 document
processing 13772 document
processing 13773 document
processing 1

processing 14052 document
processing 14053 document
processing 14054 document
processing 14055 document
processing 14056 document
processing 14057 document
processing 14058 document
processing 14059 document
processing 14060 document
processing 14061 document
processing 14062 document
processing 14063 document
processing 14064 document
processing 14065 document
processing 14066 document
processing 14067 document
processing 14068 document
processing 14069 document
processing 14070 document
processing 14071 document
processing 14072 document
processing 14073 document
processing 14074 document
processing 14075 document
processing 14076 document
processing 14077 document
processing 14078 document
processing 14079 document
processing 14080 document
processing 14081 document
processing 14082 document
processing 14083 document
processing 14084 document
processing 14085 document
processing 14086 document
processing 14087 document
processing 14088 document
processing 14089 document
processing 1

processing 14369 document
processing 14370 document
processing 14371 document
processing 14372 document
processing 14373 document
processing 14374 document
processing 14375 document
processing 14376 document
processing 14377 document
processing 14378 document
processing 14379 document
processing 14380 document
processing 14381 document
processing 14382 document
processing 14383 document
processing 14384 document
processing 14385 document
processing 14386 document
processing 14387 document
processing 14388 document
processing 14389 document
processing 14390 document
processing 14391 document
processing 14392 document
processing 14393 document
processing 14394 document
processing 14395 document
processing 14396 document
processing 14397 document
processing 14398 document
processing 14399 document
processing 14400 document
processing 14401 document
processing 14402 document
processing 14403 document
processing 14404 document
processing 14405 document
processing 14406 document
processing 1

processing 14686 document
processing 14687 document
processing 14688 document
processing 14689 document
processing 14690 document
processing 14691 document
processing 14692 document
processing 14693 document
processing 14694 document
processing 14695 document
processing 14696 document
processing 14697 document
processing 14698 document
processing 14699 document
processing 14700 document
processing 14701 document
processing 14702 document
processing 14703 document
processing 14704 document
processing 14705 document
processing 14706 document
processing 14707 document
processing 14708 document
processing 14709 document
processing 14710 document
processing 14711 document
processing 14712 document
processing 14713 document
processing 14714 document
processing 14715 document
processing 14716 document
processing 14717 document
processing 14718 document
processing 14719 document
processing 14720 document
processing 14721 document
processing 14722 document
processing 14723 document
processing 1

In [38]:
data['text']

['xref cantaloupe srv cs cmu edu alt atheism alt atheism moderated news answers alt answers path cantaloupe srv cs cmu edu crabapple srv cs cmu edu bb andrew cmu edu news sei cmu edu cis ohio state edu magnus acs ohio state edu usenet ins cwru edu agate spool mu edu uunet pipex ibmpcug mantis mathew from mathew mathew mantis co uk newsgroups alt atheism alt atheism moderated news answers alt answers subject alt atheism faq atheist resources summary books addresses music anything related to atheism keywords faq atheism books music fiction addresses contacts message id mantis co uk date mon mar gmt expires thu apr gmt followup to alt atheism distribution world organization mantis consultants cambridge uk approved news answers request mit edu supersedes mantis co uk lines archive name atheism resources alt atheism archive name resources last modified december version atheist resources addresses of atheist organizations usa freedom from religion foundation darwin fish bumper stickers and a

In [39]:
# save the model to disk
import pickle
filename = 'data.pkl'
pickle.dump(data, open(filename, 'wb'))

In [40]:
#import pickle
#data = pickle.load(open('data.pkl', 'rb'))

In [41]:
pd.DataFrame(data).head()

index                                               text  target  \
0      0  xref cantaloupe srv cs cmu edu alt atheism alt...       0   
1      1  xref cantaloupe srv cs cmu edu alt atheism alt...       0   
2      2  newsgroups alt atheism path cantaloupe srv cs ...       0   
3      3  xref cantaloupe srv cs cmu edu alt atheism alt...       0   
4      4  xref cantaloupe srv cs cmu edu alt atheism soc...       0   

   word_count                                 clean_text_stemmed  \
0        1772  [cantaloup, srv, cs, cmu, edu, alt, atheism, a...   
1        5425  [cantaloup, srv, cs, cmu, edu, alt, atheism, a...   
2         806  [newsgroup, alt, atheism, path, cantaloup, srv...   
3         325  [cantaloup, srv, cs, cmu, edu, alt, atheism, a...   
4         206  [cantaloup, srv, cs, cmu, edu, alt, atheism, s...   

                               clean_text_lemmatized  \
0  [cantaloupe, srv, cs, cmu, edu, alt, atheism, ...   
1  [cantaloupe, srv, cs, cmu, edu, alt, atheism, ...   
2  [newsgroup, alt, atheism, path, cantaloupe, sr...   
3  [cantaloupe, srv, cs, cmu, edu, alt, atheism, ...   
4  [cantaloupe, srv, cs, cmu, edu, alt, atheism, ...   

                                        text_stemmed  \
0  [xref, cantaloup, srv, cs, cmu, edu, alt, athe...   
1  [xref, cantaloup, srv, cs, cmu, edu, alt, athe...   
2  [newsgroup, alt, atheism, path, cantaloup, srv...   
3  [xref, cantaloup, srv, cs, cmu, edu, alt, athe...   
4  [xref, cantaloup, srv, cs, cmu, edu, alt, athe...   

                                     text_lemmatized  
0  [xref, cantaloupe, srv, cs, cmu, edu, alt, ath...  
1  [xref, cantaloupe, srv, cs, cmu, edu, alt, ath...  
2  [newsgroup, alt, atheism, path, cantaloupe, sr...  
3  [xref, cantaloupe, srv, cs, cmu, edu, alt, ath...  
4  [xref, cantaloupe, srv, cs, cmu, edu, alt, ath...

In [42]:
data['clean_text_lemmatized']

[['cantaloupe',
  'srv',
  'cs',
  'cmu',
  'edu',
  'alt',
  'atheism',
  'alt',
  'atheism',
  'moderate',
  'news',
  'answer',
  'alt',
  'answer',
  'path',
  'cantaloupe',
  'srv',
  'cs',
  'cmu',
  'edu',
  'crabapple',
  'srv',
  'cs',
  'cmu',
  'edu',
  'bb',
  'andrew',
  'cmu',
  'edu',
  'news',
  'sei',
  'cmu',
  'edu',
  'cis',
  'ohio',
  'state',
  'edu',
  'magnus',
  'acs',
  'ohio',
  'state',
  'edu',
  'usenet',
  'in',
  'cwru',
  'edu',
  'agate',
  'spool',
  'mu',
  'edu',
  'uunet',
  'pipex',
  'ibmpcug',
  'mantis',
  'mathew',
  'mathew',
  'mathew',
  'mantis',
  'co',
  'uk',
  'newsgroup',
  'alt',
  'atheism',
  'alt',
  'atheism',
  'moderate',
  'news',
  'answer',
  'alt',
  'answer',
  'subject',
  'alt',
  'atheism',
  'faq',
  'atheist',
  'resource',
  'summary',
  'book',
  'address',
  'music',
  'relate',
  'atheism',
  'keyword',
  'faq',
  'atheism',
  'book',
  'music',
  'fiction',
  'address',
  'contact',
  'message',
  'd',
  'mantis

In [43]:
print("Data Type: ",type(data['text']))
print("Data Type: ",type(data['clean_text_stemmed']))

print("Length of data: ",len(data['text']))
print("Length of data: ",len(data['clean_text_stemmed']))

Data Type:  <class 'list'>
Data Type:  <class 'list'>
Length of data:  14996
Length of data:  14996


In [44]:
print(data['text'][1])
print("************************************************************")

print("\n clean_text_stemmed \n")
print(data['clean_text_stemmed'][1])

print("************************************************************")
print("\n clean_text_lemmatized \n")
print(data['clean_text_lemmatized'][1])

xref cantaloupe srv cs cmu edu alt atheism alt atheism moderated news answers alt answers path cantaloupe srv cs cmu edu crabapple srv cs cmu edu fs ece cmu edu europa eng gtefsd com howland reston ans net agate netsys ibmpcug mantis mathew from mathew mathew mantis co uk newsgroups alt atheism alt atheism moderated news answers alt answers subject alt atheism faq introduction to atheism summary please read this file before posting to alt atheism keywords faq atheism message id mantis co uk date mon apr gmt expires thu may gmt followup to alt atheism distribution world organization mantis consultants cambridge uk approved news answers request mit edu supersedes mantis co uk lines archive name atheism introduction alt atheism archive name introduction last modified april version begin pgp signed message an introduction to atheism by mathew mathew mantis co uk this article attempts to provide a general introduction to atheism whilst i have tried to be as neutral as possible regarding con

# TF-IDF

In [45]:
## tfidf vectorizer needs sentence and not token. Hence we need to combine all the tokens back to form a string

data['clean_text_stemmed'] = [' '.join(text) for text in data['clean_text_stemmed']]
data['clean_text_lemmatized'] = [' '.join(text) for text in data['clean_text_lemmatized']]
data['clean_text_lemmatized'][0]

'cantaloupe srv cs cmu edu alt atheism alt atheism moderate news answer alt answer path cantaloupe srv cs cmu edu crabapple srv cs cmu edu bb andrew cmu edu news sei cmu edu cis ohio state edu magnus acs ohio state edu usenet in cwru edu agate spool mu edu uunet pipex ibmpcug mantis mathew mathew mathew mantis co uk newsgroup alt atheism alt atheism moderate news answer alt answer subject alt atheism faq atheist resource summary book address music relate atheism keyword faq atheism book music fiction address contact message d mantis co uk date mon mar gmt expire thu apr gmt followup alt atheism distribution world organization mantis consultant cambridge uk approve news answer request mit edu supersede mantis co uk line archive atheism resource alt atheism archive resource modify december version atheist resource address atheist organization usa freedom religion foundation darwin fish bumper sticker assorted atheist paraphernalia available freedom religion foundation write ffrf p o box 

In [46]:
from sklearn.feature_extraction.text import TfidfVectorizer

#define vectorizer parameters
tfidf_vectorizer = TfidfVectorizer(max_df=0.95,
                                 min_df=0.05,
                                 use_idf=True, ngram_range=(1,4))  
#got 65% val accuracy with max_df=0.9,min_df=0.2
#got 78% val accuracy with max_df=0.95,min_df=0.1
#got 94% val accuracy with max_df=0.95,min_df=0.05
#tfidf_vectorizer = TfidfVectorizer()    giving 1 lakh features
tfidf_matrix = tfidf_vectorizer.fit_transform(data['clean_text_lemmatized'])

print(tfidf_matrix.shape)

(14996, 823)


In [47]:
tfidf_matrix1=pd.DataFrame(tfidf_matrix.toarray(), columns= tfidf_vectorizer.get_feature_names()) # Array mapping from feature integer indices to feature name

In [48]:
tfidf_matrix1.head()

able   ac   accept  access   account     act    action  actually  add  \
0  0.00000  0.0  0.00000     0.0  0.027420  0.0000  0.000000   0.00000  0.0   
1  0.00826  0.0  0.01834     0.0  0.000000  0.0568  0.028436   0.02303  0.0   
2  0.00000  0.0  0.09392     0.0  0.049154  0.0000  0.000000   0.00000  0.0   
3  0.00000  0.0  0.00000     0.0  0.000000  0.0000  0.000000   0.00000  0.0   
4  0.00000  0.0  0.00000     0.0  0.000000  0.0000  0.000000   0.00000  0.0   

    address  ...  write article  write article apr     wrong    wupost  \
0  0.132597  ...            0.0                0.0  0.000000  0.000000   
1  0.000000  ...            0.0                0.0  0.024468  0.000000   
2  0.000000  ...            0.0                0.0  0.000000  0.000000   
3  0.000000  ...            0.0                0.0  0.000000  0.098044   
4  0.000000  ...            0.0                0.0  0.000000  0.073107   

       year       yes  zaphod  zaphod mp  zaphod mp ohio  zaphod mp ohio state  
0  0.000000  0.000000     0.0        0.0             0.0                   0.0  
1  0.012066  0.008207     0.0        0.0             0.0                   0.0  
2  0.000000  0.000000     0.0        0.0             0.0                   0.0  
3  0.000000  0.000000     0.0        0.0             0.0                   0.0  
4  0.000000  0.000000     0.0        0.0             0.0                   0.0  

[5 rows x 823 columns]

In [49]:
terms = tfidf_vectorizer.get_feature_names()
print(type(terms))
terms[:5]

<class 'list'>


['able', 'ac', 'accept', 'access', 'account']

In [50]:
#Duplicating the original text extracted before proceeeding with preprocessing steps

import copy
train_data = copy.deepcopy(tfidf_matrix1)

In [51]:
train_data['target']=data['target']

In [52]:
train_data.head()

able   ac   accept  access   account     act    action  actually  add  \
0  0.00000  0.0  0.00000     0.0  0.027420  0.0000  0.000000   0.00000  0.0   
1  0.00826  0.0  0.01834     0.0  0.000000  0.0568  0.028436   0.02303  0.0   
2  0.00000  0.0  0.09392     0.0  0.049154  0.0000  0.000000   0.00000  0.0   
3  0.00000  0.0  0.00000     0.0  0.000000  0.0000  0.000000   0.00000  0.0   
4  0.00000  0.0  0.00000     0.0  0.000000  0.0000  0.000000   0.00000  0.0   

    address  ...  write article apr     wrong    wupost      year       yes  \
0  0.132597  ...                0.0  0.000000  0.000000  0.000000  0.000000   
1  0.000000  ...                0.0  0.024468  0.000000  0.012066  0.008207   
2  0.000000  ...                0.0  0.000000  0.000000  0.000000  0.000000   
3  0.000000  ...                0.0  0.000000  0.098044  0.000000  0.000000   
4  0.000000  ...                0.0  0.000000  0.073107  0.000000  0.000000   

   zaphod  zaphod mp  zaphod mp ohio  zaphod mp ohio state  target  
0     0.0        0.0             0.0                   0.0       0  
1     0.0        0.0             0.0                   0.0       0  
2     0.0        0.0             0.0                   0.0       0  
3     0.0        0.0             0.0                   0.0       0  
4     0.0        0.0             0.0                   0.0       0  

[5 rows x 824 columns]

# Splitting Data into Train and Validation

In [53]:
train_data_new=train_data.sample(frac=0.8,random_state=200) #random state is a seed value
val_data=train_data.drop(train_data_new.index)

In [54]:
#Performing train val split on the data
X_train, y_train = train_data_new.loc[:,train_data_new.columns!='target'], train_data_new.loc[:,'target']

X_val, y_val = val_data.loc[:,val_data.columns!='target'], val_data.loc[:,'target']

In [55]:
print(X_train.shape)
print(y_train.shape)
print(X_val.shape)
print(y_val.shape)

(11997, 823)
(11997,)
(2999, 823)
(2999,)


# Preparation for Model buillding



## Classification report

In [56]:
def get_CR_CM(train_actual,train_predicted,test_actual,test_predicted):
    print('''
         ========================================
           CLASSIFICATION REPORT FOR TRAIN DATA
         ========================================
        ''')
    print(classification_report(train_actual, train_predicted, digits=4))

    print('''
             =============================================
               CLASSIFICATION REPORT FOR VALIDATION DATA
             =============================================
            ''')
    print(classification_report(test_actual, test_predicted, digits=4))
    

## Function to calculate accuracy, recall, precision and F1 score# 

In [57]:
scores = pd.DataFrame(columns=['Model','Train_Accuracy','Train_Recall','Train_Precision','Train_F1_Score','Test_Accuracy','Test_Recall','Test_Precision','Test_F1_Score'])

def get_metrics(train_actual,train_predicted,test_actual,test_predicted,model_description,dataframe):
    get_CR_CM(train_actual,train_predicted,test_actual,test_predicted)
    train_accuracy = accuracy_score(train_actual,train_predicted)
    train_recall   = recall_score(train_actual,train_predicted,average ='weighted')
    train_precision= precision_score(train_actual,train_predicted,average ='weighted')
    train_f1score  = f1_score(train_actual,train_predicted,average ='weighted')
    test_accuracy = accuracy_score(test_actual,test_predicted)
    test_recall   = recall_score(test_actual,test_predicted,average ='weighted')
    test_precision= precision_score(test_actual,test_predicted,average ='weighted')
    test_f1score  = f1_score(test_actual,test_predicted,average ='weighted')
    dataframe = dataframe.append(pd.Series([model_description, train_accuracy,train_recall,train_precision,train_f1score,
                                            test_accuracy,test_recall,test_precision,test_f1score],
                                           index=scores.columns ), ignore_index=True)
    return(dataframe)

# MODEL BUILDING

## Logistic Regression

In [58]:
from sklearn.linear_model import LogisticRegression
log_mod = LogisticRegression(random_state=123)

In [59]:
log_mod.fit(X_train, y_train)

LogisticRegression(random_state=123)

In [60]:
y_pred_train = log_mod.predict(X_train)
y_pred_val = log_mod.predict(X_val)

##### Evaluating the model performance

In [64]:
from sklearn.metrics import classification_report
from sklearn.metrics import accuracy_score,recall_score,precision_score,f1_score

In [65]:
scores = get_metrics(y_train,y_pred_train,y_val,y_pred_val,"Logistic",scores)
scores


           CLASSIFICATION REPORT FOR TRAIN DATA
        
              precision    recall  f1-score   support

           0     0.9047    0.8452    0.8739       730
           1     0.9607    0.9402    0.9503       468
           2     0.9705    0.9825    0.9765       570
           3     0.9574    0.9836    0.9704       549
           4     0.9721    0.9868    0.9794       530
           5     0.9562    0.9544    0.9553       526
           6     0.9748    0.9169    0.9450       337
           7     0.9741    0.9878    0.9809       572
           8     0.9984    1.0000    0.9992       610
           9     0.9981    0.9981    0.9981       539
          10     0.9983    0.9983    0.9983       589
          11     0.9957    0.9871    0.9914       697
          12     0.9683    0.9752    0.9717       564
          13     0.9916    0.9866    0.9891       599
          14     0.9936    0.9952    0.9944       627
          15     0.9953    0.9953    0.9953       638
          16     0.9375

Model  Train_Accuracy  Train_Recall  Train_Precision  Train_F1_Score  \
0  Logistic        0.955155      0.955155         0.956565        0.955266   

   Test_Accuracy  Test_Recall  Test_Precision  Test_F1_Score  
0       0.937312     0.937312        0.938403       0.937355

# Ridge Regression

In [66]:
from sklearn.linear_model import RidgeClassifierCV

In [67]:
#### TYPE
ridge_model=RidgeClassifierCV(fit_intercept=True, alphas=[0.0125, 0.025, 0.05,.1, .125, .25, .5, 1., 2., 4.,10,100])

In [68]:
ridge_model.fit(X_train,y_train)

RidgeClassifierCV(alphas=array([1.25e-02, 2.50e-02, 5.00e-02, 1.00e-01, 1.25e-01, 2.50e-01,
       5.00e-01, 1.00e+00, 2.00e+00, 4.00e+00, 1.00e+01, 1.00e+02]))

In [69]:
y_pred_train = ridge_model.predict(X_train)
y_pred_val = ridge_model.predict(X_val)

##### Evaluating the model performance

In [70]:
scores = get_metrics(y_train,y_pred_train,y_val,y_pred_val,"Ridge",scores)
scores


           CLASSIFICATION REPORT FOR TRAIN DATA
        
              precision    recall  f1-score   support

           0     0.9665    0.7904    0.8696       730
           1     0.9626    0.9338    0.9479       468
           2     0.9823    0.9737    0.9780       570
           3     0.9627    0.9872    0.9748       549
           4     0.9563    0.9906    0.9731       530
           5     0.9669    0.9430    0.9548       526
           6     0.9784    0.9407    0.9592       337
           7     0.9809    0.9878    0.9843       572
           8     1.0000    0.9967    0.9984       610
           9     1.0000    0.9981    0.9991       539
          10     0.9983    1.0000    0.9992       589
          11     0.9957    0.9943    0.9950       697
          12     0.9668    0.9805    0.9736       564
          13     0.9818    0.9900    0.9859       599
          14     0.9968    0.9968    0.9968       627
          15     1.0000    1.0000    1.0000       638
          16     0.9375

Model  Train_Accuracy  Train_Recall  Train_Precision  Train_F1_Score  \
0  Logistic        0.955155      0.955155         0.956565        0.955266   
1     Ridge        0.956656      0.956656         0.961149        0.956864   

   Test_Accuracy  Test_Recall  Test_Precision  Test_F1_Score  
0       0.937312     0.937312        0.938403       0.937355  
1       0.949983     0.949983        0.953609       0.950081

# LASSO

In [71]:
lasso=LogisticRegression(penalty='l1', solver='liblinear')

In [72]:
lasso.fit(X_train,y_train)

LogisticRegression(penalty='l1', solver='liblinear')

In [73]:
y_pred_train = lasso.predict(X_train)
y_pred_val = lasso.predict(X_val)

##### Evaluating the model performance

In [74]:
scores = get_metrics(y_train,y_pred_train,y_val,y_pred_val,"LASSO",scores)
scores


           CLASSIFICATION REPORT FOR TRAIN DATA
        
              precision    recall  f1-score   support

           0     0.9452    0.8041    0.8690       730
           1     0.9442    0.9402    0.9422       468
           2     0.9724    0.9877    0.9800       570
           3     0.9729    0.9818    0.9773       549
           4     0.9793    0.9830    0.9812       530
           5     0.9706    0.9430    0.9566       526
           6     0.9611    0.9525    0.9568       337
           7     0.9843    0.9895    0.9869       572
           8     1.0000    1.0000    1.0000       610
           9     1.0000    0.9963    0.9981       539
          10     0.9983    1.0000    0.9992       589
          11     0.9957    0.9928    0.9943       697
          12     0.9684    0.9787    0.9735       564
          13     0.9883    0.9883    0.9883       599
          14     0.9921    0.9984    0.9952       627
          15     0.9938    1.0000    0.9969       638
          16     0.9347

Model  Train_Accuracy  Train_Recall  Train_Precision  Train_F1_Score  \
0  Logistic        0.955155      0.955155         0.956565        0.955266   
1     Ridge        0.956656      0.956656         0.961149        0.956864   
2     LASSO        0.955656      0.955656         0.959101        0.955841   

   Test_Accuracy  Test_Recall  Test_Precision  Test_F1_Score  
0       0.937312     0.937312        0.938403       0.937355  
1       0.949983     0.949983        0.953609       0.950081  
2       0.952651     0.952651        0.955385       0.952676

# Naive Bayes

In [75]:
from sklearn import model_selection, naive_bayes, svm

In [76]:
# fit the training dataset on the NB classifier
Naive = naive_bayes.MultinomialNB()
Naive.fit(X_train,y_train)

# predict the labels on train dataset
y_pred_train = Naive.predict(X_train)

# predict the labels on validation dataset
y_pred_val = Naive.predict(X_val)

In [77]:
scores = get_metrics(y_train,y_pred_train,y_val,y_pred_val,"Naive Bayes",scores)
scores


           CLASSIFICATION REPORT FOR TRAIN DATA
        
              precision    recall  f1-score   support

           0     0.7796    0.8479    0.8123       730
           1     0.9295    0.7885    0.8532       468
           2     0.9298    0.9754    0.9521       570
           3     0.8889    0.9909    0.9371       549
           4     0.9210    0.9453    0.9330       530
           5     0.8834    0.8498    0.8663       526
           6     0.9478    0.6469    0.7690       337
           7     0.8797    0.8951    0.8873       572
           8     0.9005    0.9492    0.9242       610
           9     0.9876    0.8868    0.9345       539
          10     0.9065    0.9881    0.9456       589
          11     0.9413    0.9656    0.9533       697
          12     0.8308    0.7837    0.8066       564
          13     0.9410    0.8781    0.9085       599
          14     0.8737    0.9601    0.9149       627
          15     0.9830    0.9984    0.9907       638
          16     0.8393

Model  Train_Accuracy  Train_Recall  Train_Precision  Train_F1_Score  \
0     Logistic        0.955155      0.955155         0.956565        0.955266   
1        Ridge        0.956656      0.956656         0.961149        0.956864   
2        LASSO        0.955656      0.955656         0.959101        0.955841   
3  Naive Bayes        0.885721      0.885721         0.886548        0.884115   

   Test_Accuracy  Test_Recall  Test_Precision  Test_F1_Score  
0       0.937312     0.937312        0.938403       0.937355  
1       0.949983     0.949983        0.953609       0.950081  
2       0.952651     0.952651        0.955385       0.952676  
3       0.872291     0.872291        0.874986       0.871139

# SVM

In [78]:
from sklearn.svm import SVC

In [79]:
svc_model=SVC()
#svc_line.set_params(classifier__kernel='linear',classifier__C=1,classifier__random_state=123)

In [80]:
svc_model.fit(X_train,y_train)

SVC()

In [81]:
y_pred_train = svc_model.predict(X_train)
y_pred_val = svc_model.predict(X_val)

In [82]:
scores = get_metrics(y_train,y_pred_train,y_val,y_pred_val,"SVM",scores)
scores


           CLASSIFICATION REPORT FOR TRAIN DATA
        
              precision    recall  f1-score   support

           0     0.9767    0.8027    0.8812       730
           1     0.9847    0.9658    0.9752       468
           2     0.9861    0.9947    0.9904       570
           3     0.9647    0.9945    0.9794       549
           4     0.9943    0.9906    0.9924       530
           5     0.9885    0.9829    0.9857       526
           6     0.9969    0.9674    0.9819       337
           7     0.9913    0.9965    0.9939       572
           8     1.0000    1.0000    1.0000       610
           9     1.0000    0.9981    0.9991       539
          10     0.9983    1.0000    0.9992       589
          11     0.9986    0.9971    0.9978       697
          12     0.9893    0.9876    0.9885       564
          13     0.9966    0.9933    0.9950       599
          14     0.9952    0.9984    0.9968       627
          15     1.0000    1.0000    1.0000       638
          16     0.9427

Model  Train_Accuracy  Train_Recall  Train_Precision  Train_F1_Score  \
0     Logistic        0.955155      0.955155         0.956565        0.955266   
1        Ridge        0.956656      0.956656         0.961149        0.956864   
2        LASSO        0.955656      0.955656         0.959101        0.955841   
3  Naive Bayes        0.885721      0.885721         0.886548        0.884115   
4          SVM        0.966075      0.966075         0.970738        0.966278   

   Test_Accuracy  Test_Recall  Test_Precision  Test_F1_Score  
0       0.937312     0.937312        0.938403       0.937355  
1       0.949983     0.949983        0.953609       0.950081  
2       0.952651     0.952651        0.955385       0.952676  
3       0.872291     0.872291        0.874986       0.871139  
4       0.941647     0.941647        0.945566       0.941824

## Random Search CV

In [83]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV

In [84]:
clf_svc=Pipeline(steps=[('classifier',SVC())])

In [85]:

svc_param_random={'classifier__C':[0.001,0.01,0.1,1,10,100],'classifier__gamma':[0,0.0001,0.01,0.1,1,10,100],
               "classifier__kernel":['linear','rbf','poly']}

In [86]:
svc_random=RandomizedSearchCV(clf_svc,param_distributions=svc_param_random,cv=3)

In [87]:
%%time
svc_random.fit(X_train,y_train)

Wall time: 1h 30min 19s


RandomizedSearchCV(cv=3, estimator=Pipeline(steps=[('classifier', SVC())]),
                   param_distributions={'classifier__C': [0.001, 0.01, 0.1, 1,
                                                          10, 100],
                                        'classifier__gamma': [0, 0.0001, 0.01,
                                                              0.1, 1, 10, 100],
                                        'classifier__kernel': ['linear', 'rbf',
                                                               'poly']})

In [88]:
# save the model to disk
import pickle
filename = 'svc_random.pkl'
pickle.dump(svc_random, open(filename, 'wb'))

In [89]:
y_pred_train = svc_random.predict(X_train)
y_pred_val = svc_random.predict(X_val)

In [90]:
scores = get_metrics(y_train,y_pred_train,y_val,y_pred_val,"SVM_grid",scores)
scores


           CLASSIFICATION REPORT FOR TRAIN DATA
        
              precision    recall  f1-score   support

           0     0.9766    0.8000    0.8795       730
           1     0.9826    0.9658    0.9741       468
           2     0.9861    0.9947    0.9904       570
           3     0.9647    0.9945    0.9794       549
           4     0.9943    0.9906    0.9924       530
           5     0.9885    0.9810    0.9847       526
           6     0.9969    0.9674    0.9819       337
           7     0.9913    0.9965    0.9939       572
           8     1.0000    1.0000    1.0000       610
           9     1.0000    0.9981    0.9991       539
          10     0.9983    1.0000    0.9992       589
          11     0.9986    0.9971    0.9978       697
          12     0.9893    0.9876    0.9885       564
          13     0.9966    0.9933    0.9950       599
          14     0.9952    0.9984    0.9968       627
          15     1.0000    1.0000    1.0000       638
          16     0.9414

Model  Train_Accuracy  Train_Recall  Train_Precision  Train_F1_Score  \
0     Logistic        0.955155      0.955155         0.956565        0.955266   
1        Ridge        0.956656      0.956656         0.961149        0.956864   
2        LASSO        0.955656      0.955656         0.959101        0.955841   
3  Naive Bayes        0.885721      0.885721         0.886548        0.884115   
4          SVM        0.966075      0.966075         0.970738        0.966278   
5     SVM_grid        0.965741      0.965741         0.970463        0.965950   

   Test_Accuracy  Test_Recall  Test_Precision  Test_F1_Score  
0       0.937312     0.937312        0.938403       0.937355  
1       0.949983     0.949983        0.953609       0.950081  
2       0.952651     0.952651        0.955385       0.952676  
3       0.872291     0.872291        0.874986       0.871139  
4       0.941647     0.941647        0.945566       0.941824  
5       0.943981     0.943981        0.947886       0.944131